In [1]:
import numpy as np
import pandas as pd
import scipy.sparse

from sklearn.feature_extraction.text import CountVectorizer
from sklearn.decomposition import TruncatedSVD
import string
from os import listdir
import os
import errno
import subprocess
from collections import defaultdict
import operator
import re
import pickle
from collections import OrderedDict
import six # needed for Google Cloud client


In [2]:
!pip install unidecode
import unidecode

In [3]:
#!pip install --upgrade --ignore-installed google-cloud-language
# Imports the Google Cloud client library
from google.cloud import language
from google.cloud.language import enums
from google.cloud.language import types

In [4]:
from tqdm import tqdm
tqdm.pandas()

In [5]:
!ls -lr recipes

total 252208
-rw-rw-r-- 1 apanza apanza 13130637 Aug 14 06:18 world-cuisine.json
-rw-rw-r-- 1 apanza apanza  5391397 Aug 15 02:07 us-recipes.json
-rw-rw-r-- 1 apanza apanza  6253027 Aug 15 13:38 soups-stews-and-chili.json
-rw-rw-r-- 1 apanza apanza  6077216 Aug 16 02:33 side-dish.json
-rw-rw-r-- 1 apanza apanza  5530495 Aug 16 05:44 seafood.json
-rw-rw-r-- 1 apanza apanza  4363583 Aug 17 01:04 salad.json
-rw-rw-r-- 1 apanza apanza  6064790 Aug 13 01:01 pasta-and-noodles.json
-rw-rw-r-- 1 apanza apanza 22297686 Aug 12 20:18 meat-and-poultry.json
-rw-rw-r-- 1 apanza apanza 22103562 Aug 12 06:09 main-dish.json
-rw-rw-r-- 1 apanza apanza  1239579 Aug 11 17:47 lunch.json
-rw-rw-r-- 1 apanza apanza 17783780 Aug 11 17:01 holidays-and-events.json
-rw-rw-r-- 1 apanza apanza  5211522 Aug 11 04:49 healthy-recipes.json
-rw-rw-r-- 1 apanza apanza 33283609 Aug 11 00:26 fruits-and-vegetables.json
-rw-rw-r-- 1 apanza apanza 40589000 Aug 10 06:50 everyday-cooking.json
-rw-rw-r-- 1 apanza apanza 2211916

In [6]:
recipe_dirname = 'recipes'
try:
    os.makedirs(recipe_dirname)
except OSError as e:
    if e.errno != errno.EEXIST:
        raise

In [7]:
datafiles = [
    'everyday-cooking.json',
    'fruits-and-vegetables.json',
    'pasta-and-noodles.json',
    'allRecipes_tony_categories.json',
    'main-dish.json',
    'meat-and-poultry.json',
    'lunch.json',
    'healthy-recipes.json',
    'holidays-and-events.json',
    'us-recipes.json',
    'world-cuisine.json', # might be a subset of ethnic_categories.json?
    'ethnic_categories.json',
    'salad.json',
    'seafood.json',
    'side-dish.json',
    'soups-stews-and-chili.json',
]

for filename in datafiles:
    if not os.path.isfile(os.path.join(recipe_dirname, filename)):
        print "Need to download: {}".format(os.path.join(recipe_dirname, filename))
        # TODO: use boto3 to download file
        subprocess.call(['aws', 's3', 'cp', 's3://RecipeVectors/'+filename, recipe_dirname])
    else:
        print "datafile already present: {}".format(os.path.join(recipe_dirname, filename))

datafile already present: recipes/everyday-cooking.json
datafile already present: recipes/fruits-and-vegetables.json
datafile already present: recipes/pasta-and-noodles.json
datafile already present: recipes/allRecipes_tony_categories.json
datafile already present: recipes/main-dish.json
datafile already present: recipes/meat-and-poultry.json
datafile already present: recipes/lunch.json
datafile already present: recipes/healthy-recipes.json
datafile already present: recipes/holidays-and-events.json
datafile already present: recipes/us-recipes.json
datafile already present: recipes/world-cuisine.json
datafile already present: recipes/ethnic_categories.json
datafile already present: recipes/salad.json
datafile already present: recipes/seafood.json
datafile already present: recipes/side-dish.json
datafile already present: recipes/soups-stews-and-chili.json


In [15]:
df =pd.DataFrame()
cnt=0
for file in listdir('recipes'):
#    print 'recipes/'+file
    if file != 'bhg_recipes.json':
        df = df.append(pd.read_json('recipes/'+file, dtype={}))
        print 'Loaded {0} recipes from {1}'.format(len(df)-cnt,file)
        cnt=len(df)
print 'Total {0}'.format(len(df))
df=df[df.duplicated(subset='url', keep='first')] 
df.drop_duplicates(subset='url', keep='first', inplace=True)
print 'Total after dropping duplicates {0}'.format(len(df))
df.sample(5)

Loaded 29453 recipes from everyday-cooking.json
Loaded 24107 recipes from fruits-and-vegetables.json
Loaded 3969 recipes from pasta-and-noodles.json
Loaded 4716 recipes from side-dish.json
Loaded 3527 recipes from salad.json
Loaded 3810 recipes from seafood.json
Loaded 28877 recipes from allRecipes_tony_categories.json
Loaded 14442 recipes from ethnic_categories.json
Loaded 3799 recipes from us-recipes.json
Loaded 4255 recipes from soups-stews-and-chili.json
Loaded 14456 recipes from main-dish.json
Loaded 14729 recipes from meat-and-poultry.json
Loaded 880 recipes from lunch.json
Loaded 4235 recipes from healthy-recipes.json
Loaded 8863 recipes from world-cuisine.json
Loaded 12679 recipes from holidays-and-events.json
Total 176797
Total after dropping duplicates 49148


categories cookingTime  \
6747   [Spicy Appetizers, Meatball Appetizers, Beef A...     PT1H30M   
9253   [Scottish Recipes, Walnut Desserts, Nut Desser...        PT2H   
13134  [Date Cookies, Fruit Cookies, Date Bars, Bar C...         NaN   
6787   [Compound Butters, Sauces and Condiments, Ever...        PT5M   
8336   [Main Dishes, Recipes, Green Bell Pepper Recip...       PT35M   

      description ethnicCategory fullCategoryTree  \
6747          NaN            NaN              NaN   
9253          NaN            NaN              NaN   
13134         NaN            NaN              NaN   
6787          NaN            NaN              NaN   
8336          NaN            NaN              NaN   

                                             ingredients  \
6747   [1 cup milk, 1 cup fresh bread crumbs, 2 pound...   
9253   [cooking spray, Pastry:, 1 1/2 cups butter, at...   
13134  [2 1/2 cups dates, pitted and chopped, 1/2 cup...   
6787   [4 ounces Gorgonzola cheese, 4 tablespoons uns...   
8336   [2 tablespoons olive oil, 1 onion, diced, 2 cl...   

                                        instructionSteps  \
6747   [In a mixing bowl, combine the milk and bread ...   
9253   [Combine 1 1/2 cup softened butter and cream c...   
13134  [Preheat oven to 350 degrees F (175 degrees C)...   
6787   [In a food processor, combine Gorgonzola chees...   
8336   [Heat the olive oil in large skillet over medi...   

                             name  rating  ratingCount  \
6747   Sweet and Sour Meatballs V    4.21           16   
9253      Scottish Walnut Tassies    0.00            0   
13134                 Date Bars I    3.59           43   
6787            Gorgonzola Butter    4.89           15   
8336               Pork Picadillo    4.09            8   

                                                     url  
6747   http://allrecipes.com/recipe/26665/sweet-and-s...  
9253   http://allrecipes.com/recipe/257957/scottish-w...  
13134     http://allrecipes.com/recipe/9666/date-bars-i/  
6787   http://allrecipes.com/recipe/47681/gorgonzola-...  
8336   http://allrecipes.com/recipe/212989/pork-picad...

In [16]:

categories = defaultdict(int)
for idx, row in df.iterrows():
    # print type(row['categories'])
    if  type(row['categories']) != float:
        for cat in row['categories']:
            categories[cat] += 1 
print 'Top 30 Categories:'
for item in sorted(categories.items(), reverse=True, key=operator.itemgetter(1))[:30]:
    print item

Top 30 Categories:
(u'Recipes', 48161)
(u'Everyday Cooking', 35883)
(u'Main Dishes', 15520)
(u'Desserts', 9204)
(u'Appetizers and Snacks', 4549)
(u'Side Dishes', 4507)
(u'Soups, Stews and Chili', 4093)
(u'Salad Recipes', 3365)
(u'Pasta by Shape', 3243)
(u'Chicken Breasts', 2965)
(u'Asian Recipes', 2850)
(u'Faceless Recipes', 2791)
(u'Bread Recipes', 2758)
(u'Soup', 2748)
(u'Fruit Desserts', 2685)
(u'Cookies', 2676)
(u'Italian Recipes', 2484)
(u'Cake Recipes', 2439)
(u'Breakfast and Brunch', 2438)
(u'Drinks', 2424)
(u'Vanilla Extract', 2268)
(u'Trusted Brands', 2198)
(u'Pasta Main Dishes', 2128)
(u'Mexican Recipes', 2122)
(u'Vegetable Side Dishes', 1960)
(u'Fish Recipes', 1943)
(u'Dips and Spreads', 1803)
(u'Fruits, Vegetables and Other Produce', 1729)
(u'Chocolate Desserts', 1709)
(u'Vegan Recipes', 1697)


In [17]:

def convertCookingTimeToMinutes(text):
    if type(text) == float:
        return None
    text = text.replace('PT','')
    arr = re.findall(r'[0-9]+', text)
    minute = 0
    if len(arr) == 2:
        minute = int(arr[0])* 60 + int(arr[1])
    if len(arr) == 1:
        if 'M' in text:
            minute = int(arr[0])
        if 'H' in text:
            minute = int(arr[0]) * 60
    return minute
df['cookingTimeMinutes'] = df['cookingTime'].apply(convertCookingTimeToMinutes)
df[['cookingTime','cookingTimeMinutes']].sample(5)

cookingTime  cookingTimeMinutes
2803         PT6M                 6.0
14976      PT3H5M               185.0
9030        PT22M                22.0
3883        PT55M                55.0
3603        PT40M                40.0

In [18]:
df.to_pickle("original_recipe_data.pkl")  # where to save it, usually as a .pkl
!aws s3 cp original_recipe_data.pkl s3://RecipeVectors

upload: ./original_recipe_data.pkl to s3://RecipeVectors/original_recipe_data.pkl


In [19]:
# def ascii_encode(text):
#     return text.encode("ascii", "ignore")

#extract_ingredients(df[['ingredients']].values[867][0])

In [20]:
from cleaning_util import extract_ingredients, translate_non_alphanumerics

In [21]:
ingreds_arr_of_lists = np.squeeze(df[['ingredients']].values)
vect_extract_ingred = np.vectorize(extract_ingredients, otypes=[list])

processed_ingreds_arr_of_lists = vect_extract_ingred(ingreds_arr_of_lists)

print type(processed_ingreds_arr_of_lists)
print "Processed ingredients from {} recipes".format(len(processed_ingreds_arr_of_lists))
print processed_ingreds_arr_of_lists.size
print processed_ingreds_arr_of_lists.shape


<type 'numpy.ndarray'>
Processed ingredients from 49148 recipes
49148
(49148,)


In [22]:
with open('ingreds_arr_of_lists.pkl', 'wb') as f:
    pickle.dump(ingreds_arr_of_lists, f)

with open('processed_ingreds_arr_of_lists.pkl', 'wb') as f:
    pickle.dump(processed_ingreds_arr_of_lists, f)


In [23]:
flattened_ingred_list = np.hstack(processed_ingreds_arr_of_lists)
print len(flattened_ingred_list)
print flattened_ingred_list.size
print flattened_ingred_list.shape
#print flattened_ingred_list

459529
459529
(459529,)


In [24]:
unique_vocab = sorted(list(set(flattened_ingred_list)))
print unique_vocab
print "{} unique ingredients found".format(len(unique_vocab))

['', '(r) cayenne pepper sauce', '(r) condensed cream celery soup', '(r) condensed cream mushroom soup', 'abalone shell', 'absinthe', 'acai berry pulp', 'acai berry sorbet', 'acai powder', 'acai pulp (r)', 'acaipomegranate juice', 'acesulfame potassium sweetener', 'achar masala', 'achiote annatto seeds', 'achiote paste', 'achiote powder', 'achiote seed', 'achiote seeds', 'acini de pepe pasta', 'acini di pepe pasta', 'acorn squash', 'acorn squashes', 'active rapidrise yeast', 'active yeast', 'active yeast activedry yeast(r)', 'active yeast bread machine', 'active yeast rapidrise', 'addins', 'additional butter margarine', 'additional butter sugar garnish', 'additional cheddar cheese', 'additional cocktail sauce dipping', 'additional extravirgin olive oil', 'additional extravirgin olive oil brushing', 'additional extravirgin olive oil storage', 'additional garnishes', 'additional green onions', 'additional heavy cream topping', 'additional ketchup', 'additional lemon topping', 'additional

In [25]:
max(unique_vocab, key=len)

'peaches nectarines blueberries strawberries raspberries blackberries combination fruits berries'

In [26]:
with open('flattened_ingred_list.pkl', 'wb') as f:
    pickle.dump(flattened_ingred_list, f)

!aws s3 cp flattened_ingred_list.pkl s3://RecipeVectors

upload: ./flattened_ingred_list.pkl to s3://RecipeVectors/flattened_ingred_list.pkl


In [27]:
with open('unique_ingredients.pkl', 'wb') as f:
    pickle.dump(unique_vocab, f)
    
!aws s3 cp unique_ingredients.pkl s3://RecipeVectors

upload: ./unique_ingredients.pkl to s3://RecipeVectors/unique_ingredients.pkl


In [53]:
# find ingredients that contain brand names
# these are identifiable from the (r) or (tm) in the names, which unidecode puts there in place of \u00ae or \u2122
# visually inspect this list and consider adding more entries to the brand_names list in cell above, then reprocess
brand_name_ingreds = [s for s in unique_vocab if '(r)' in s or '(tm)' in s]
print len(brand_name_ingreds)
#print brand_name_ingreds
for brand_name in brand_name_ingreds:
    print brand_name

1088
(r) condensed cream celery soup
(r) condensed cream mushroom soup
active yeast activedry yeast(r)
allwhites(r) egg whites
almond extract watkins(r)
almond orgeat syrup torani(r)
almondflavored liqueur disaronno(r)
almondflavored syrup torani(r)
amaretto liqueur disaronno(r)
amaro liqueur averno(r)
amaro liqueur hum(r)
amaro liqueur luxardo(r) abano
amber beer honey brown lager(r)
american cheese cooper(r)
angostura bitters(r)
aniseflavored liqueur herbsaint(r)
annies(tm) bunny grahams(tm) honey snacks
apple juice concentrate orchard(r)
apple pie spice mccormicks(r)
apricot fruit filling baker(r) dessert
apricot fruit filling solo(r)
arepas flour pan(r)
argo(r) baking powder
argo(r) corn starch
argo(r) kingsfords(r) corn starch
aromatic bitters peychauds(r)
asian sides(tm) chicken rice
asian sweet chile sauce mae ploy(r) chilli
avocado oil acado(tm)
aylmer(r) garlic olive oil petite tomatoes
aylmer(r) italian seasonings stewed tomatoes
baby broccoli broccolini(r)
baby kale olivias(

In [28]:
flat_ingred_arr = [' '.join(lst) for lst in processed_ingreds_arr_of_lists]

print flat_ingred_arr

['roma plum tomatoes sweet onion red bell pepper yellow bell pepper cilantro lime salt', 'kiwis golden delicious apples raspberries strawberries white sugar brown sugar fruit preserves flavor flour tortillas butter flavored cooking spray cinnamon sugar', 'russet potatoes onion rings salt pepper butter flour salt milk cheddar cheese', 'butter butter flavored shortening light brown sugar white sugar eggs vanilla extract flour baking soda cinnamon salt oats raisins', 'flour salt black pepper oregano chicken breast butter olive oil mushrooms marsala wine cooking sherry', 'chicken tomatoes enchilada sauce onion green chile peppers garlic water chicken broth cumin chili powder salt black pepper bay leaf corn cilantro corn tortillas vegetable oil', 'white sugar cinnamon butter white sugar eggs bananas sour cream vanilla extract cinnamon salt baking soda flour walnuts', 'vegetable oil onion garlic quinoa vegetable broth cumin cayenne pepper salt black pepper corn kernels black beans cilantro',

In [29]:
print len(flat_ingred_arr)

49148


In [30]:
### OBSOLETE!!
# cv = CountVectorizer(vocabulary=unique_vocab)
# recipe_ingredient_matrix = cv.fit_transform(flat_ingred_arr)

# print type(recipe_ingredient_matrix)
# print recipe_ingredient_matrix.size
# print recipe_ingredient_matrix.shape
# print recipe_ingredient_matrix.nnz

# print recipe_ingredient_matrix

In [31]:
#print np.max(recipe_ingredient_matrix)

#print np.max(recipe_ingredient_matrix, axis=0) # 9
#print np.max(recipe_ingredient_matrix, axis=0).shape # (1, 18996)

#print np.max(np.max(recipe_ingredient_matrix, axis=0)) # 9

#top_ingreds = np.argwhere(recipe_ingredient_matrix[:,:] == np.max(recipe_ingredient_matrix))
#print top_ingreds.shape


#winner = np.argwhere(recipe_ingredient_matrix == np.max(recipe_ingredient_matrix, axis=1))
#print winner
#print winner.shape

#np.in1d(recipe_ingredient_matrix, [9]).reshape(recipe_ingredient_matrix.shape)

#top_ingreds_idx = np.where(recipe_ingredient_matrix == np.max(recipe_ingredient_matrix))[:,1]
#print top_ingreds_idx
#print top_ingreds_idx.shape

In [32]:
# https://stackoverflow.com/a/8980156/2491761
def save_sparse_csr(filename,array):
    np.savez(filename,data = array.data ,indices=array.indices,
             indptr =array.indptr, shape=array.shape )



In [33]:
### OBSOLETE
#save_sparse_csr("sparse_recipe_ingredient_matrix", recipe_ingredient_matrix)
#!aws s3 cp sparse_recipe_ingredient_matrix.npz s3://RecipeVectors

In [34]:
df['cleanedIngredients'] = df['ingredients'].progress_apply(extract_ingredients)
df.sample(5)

100%|██████████| 49148/49148 [01:08<00:00, 722.42it/s] 


categories cookingTime  \
4009   [Greens Side Dishes, Vegetable Side Dishes, Si...     PT1H20M   
6984   [Mexican Recipes, Everyday Cooking, Main Dishe...       PT20M   
4228   [Mashed Potatoes, Potato Side Dishes, Side Dis...     PT1H10M   
3904   [Cranberry Desserts, Banana Desserts, Fruit De...       PT30M   
18297  [Italian Recipes, Fish Recipes, Everyday Cooki...         NaN   

      description ethnicCategory fullCategoryTree  \
4009          NaN            NaN              NaN   
6984          NaN            NaN              NaN   
4228          NaN            NaN              NaN   
3904          NaN            NaN              NaN   
18297         NaN            NaN              NaN   

                                             ingredients  \
4009   [1/4 cup olive oil, 8 slices bacon, cut into 1...   
6984   [10 (6 inch) corn tortillas, 2 cups shredded m...   
4228   [1 pound potatoes, 4 cups shredded cabbage, 1 ...   
3904   [1 (15 ounce) can pear halves, drained, 1 cup ...   
18297  [4 pounds bone-in pork roast, 3 teaspoons salt...   

                                        instructionSteps  \
4009   [Heat olive oil in a large pot over medium-hig...   
6984   [Heat a large frying pan or griddle over a med...   
4228   [Place potatoes in a large pot and cover with ...   
3904   [Preheat oven to 375 degrees F (190 degrees C....   
18297  [Season pork roast with salt to taste; dredge ...   

                                    name  rating  ratingCount  \
4009   Chef Scott's Kickin' Mixed Greens    5.00            6   
6984                       Quesadillas I    4.27           33   
4228              Cream Cheese Colcannon    4.60           15   
3904              Pear Banana Berry Bake    4.47           15   
18297     Shredded Roast Spaghetti Sauce    3.00            2   

                                                     url  cookingTimeMinutes  \
4009   http://allrecipes.com/recipe/231035/chef-scott...                80.0   
6984   http://allrecipes.com/recipe/14847/quesadillas-i/                20.0   
4228   http://allrecipes.com/recipe/220491/cream-chee...                70.0   
3904   http://allrecipes.com/recipe/24122/pear-banana...                30.0   
18297  http://allrecipes.com/recipe/14783/shredded-ro...                 NaN   

                                      cleanedIngredients  
4009   [olive oil, bacon, onion, garlic, collard gree...  
6984   [corn tortillas, mozzarella cheese, black oliv...  
4228   [potatoes, cabbage, onion, skim milk, butter, ...  
3904   [pear, cranberries, banana, orange juice, whit...  
18297  [bonein pork roast, salt, flour, olive oil, wa...

In [35]:
df.to_pickle('CleanedIngredients.pkl')

In [36]:
!aws s3 cp CleanedIngredients.pkl s3://RecipeVectors

upload: ./CleanedIngredients.pkl to s3://RecipeVectors/CleanedIngredients.pkl


In [37]:
pd.set_option('display.max_colwidth', -1)
df[['cleanedIngredients']].head()

cleanedIngredients
0  [roma plum tomatoes, sweet onion, red bell pepper, yellow bell pepper, cilantro, lime, salt]                                                                                 
1  [kiwis, golden delicious apples, raspberries, strawberries, white sugar, brown sugar, fruit preserves flavor, flour tortillas, butter flavored cooking spray, cinnamon sugar]
2  [russet potatoes, onion rings, salt pepper, butter, flour, salt, milk, cheddar cheese]                                                                                       
3  [butter, butter flavored shortening, light brown sugar, white sugar, eggs, vanilla extract, flour, baking soda, cinnamon, salt, oats, raisins]                               
4  [flour, salt, black pepper, oregano, chicken breast, butter, olive oil, mushrooms, marsala wine, cooking sherry]

In [38]:
df[['ingredients']].head()

ingredients
0  [6 roma (plum) tomatoes, diced, 1 sweet onion, diced, 1 medium red bell pepper, diced, 1 medium yellow bell pepper, diced, 1 bunch cilantro, finely minced, 1 lime, juiced, 1 teaspoon salt, or to taste, Add all ingredients to list, Add all ingredients to list]                                                                                                                  
1  [2 kiwis, peeled and diced, 2 Golden Delicious apples - peeled, cored and diced, 8 ounces raspberries, 1 pound strawberries, 2 tablespoons white sugar, 1 tablespoon brown sugar, 3 tablespoons fruit preserves, any flavor, 10 (10 inch) flour tortillas, butter flavored cooking spray, 2 tablespoons cinnamon sugar, Add all ingredients to list, Add all ingredients to list]    
2  [4 russet potatoes, sliced into 1/4 inch slices, 1 onion, sliced into rings, salt and pepper to taste, 3 tablespoons butter, 3 tablespoons all-purpose flour, 1/2 teaspoon salt, 2 cups milk, 1 1/2 cups shredded Cheddar cheese, Add all ingredients to list, Add all ingredients to list]                                                                                          
3  [1/2 cup butter, softened, 1/2 cup butter flavored shortening, 1 cup packed light brown sugar, 1/2 cup white sugar, 2 eggs, 1 teaspoon vanilla extract, 1 1/2 cups all-purpose flour, 1 teaspoon baking soda, 1 teaspoon ground cinnamon, 1/2 teaspoon ground cloves, 1/2 teaspoon salt, 3 cups rolled oats, 1 cup raisins, Add all ingredients to list, Add all ingredients to list]
4  [1/4 cup all-purpose flour for coating, 1/2 teaspoon salt, 1/4 teaspoon ground black pepper, 1/2 teaspoon dried oregano, 4 skinless, boneless chicken breast halves - pounded 1/4 inch thick, 4 tablespoons butter, 4 tablespoons olive oil, 1 cup sliced mushrooms, 1/2 cup Marsala wine, 1/4 cup cooking sherry, Add all ingredients to list, Add all ingredients to list]

In [39]:
print type(df[['cleanedIngredients']].values)
print len(df[['cleanedIngredients']].values)
print df[['cleanedIngredients']].values.size
print df[['cleanedIngredients']].values.shape

np.squeeze(df[['cleanedIngredients']].values)
print type(np.squeeze(df[['cleanedIngredients']].values))
print len(np.squeeze(df[['cleanedIngredients']].values))
print np.squeeze(df[['cleanedIngredients']].values).size
print np.squeeze(df[['cleanedIngredients']].values).shape

print type(np.squeeze(df[['cleanedIngredients']].values)[3])

<type 'numpy.ndarray'>
49148
49148
(49148, 1)
<type 'numpy.ndarray'>
49148
49148
(49148,)
<type 'list'>


In [40]:
def already_tokenized(l):
    return l

cv2 = CountVectorizer(vocabulary=unique_vocab, analyzer=lambda x:x, tokenizer=lambda text: text, lowercase=False)
recipe_ingredient_matrix2 = cv2.fit_transform(np.squeeze(df[['cleanedIngredients']].values))

print type(recipe_ingredient_matrix2)
print recipe_ingredient_matrix2.size
print recipe_ingredient_matrix2.nnz
print recipe_ingredient_matrix2.shape

#print recipe_ingredient_matrix2
#print np.max(recipe_ingredient_matrix2)

<class 'scipy.sparse.csr.csr_matrix'>
447861
447861
(49148, 18408)


In [41]:
#print np.max(recipe_ingredient_matrix2)
np.set_printoptions(threshold=np.nan)

#dt = np.dtype('int,float')

ingred_counts = zip(cv2.get_feature_names(), np.asarray(recipe_ingredient_matrix2.sum(axis=0)).ravel())

#ingred_counts_arr = np.asarray(ingred_counts, dtype=dt)

In [42]:
df_ingred_counts = pd.DataFrame(ingred_counts, columns=['ingredient', 'count'])

In [43]:
df_ingred_counts.head(15)

ingredient  count
0                                      12   
1   (r) cayenne pepper sauce           1    
2   (r) condensed cream celery soup    1    
3   (r) condensed cream mushroom soup  3    
4   abalone shell                      2    
5   absinthe                           2    
6   acai berry pulp                    5    
7   acai berry sorbet                  1    
8   acai powder                        1    
9   acai pulp (r)                      1    
10  acaipomegranate juice              1    
11  acesulfame potassium sweetener     1    
12  achar masala                       1    
13  achiote annatto seeds              4    
14  achiote paste                      2

In [44]:
from IPython.display import display
display(df_ingred_counts.sort(columns='count', ascending=False))

/home/apanza/anaconda2/lib/python2.7/site-packages/ipykernel/__main__.py:2: FutureWarning: sort(columns=....) is deprecated, use sort_values(by=.....)
  from ipykernel import kernelapp as app


ingredient  count
14201  salt                                       16983
2274   butter                                     14365
17955  white sugar                                12331
6553   garlic                                     11532
6197   flour                                      10033
10997  onion                                      9701 
17565  water                                      9694 
1598   black pepper                               8094 
10952  olive oil                                  7880 
5618   eggs                                       7760 
10328  milk                                       6405 
17126  vanilla extract                            5458 
17299  vegetable oil                              5164 
3904   cinnamon                                   5036 
2166   brown sugar                                4359 
14204  salt black pepper                          3881 
14221  salt pepper                                3705 
9159   lemon juice                                3585 
5565   egg                                        3448 
815    baking powder                              3440 
11402  parsley                                    3086 
11360  parmesan cheese                            3036 
817    baking soda                                2943 
2933   cheddar cheese                             2932 
6627   garlic powder                              2826 
16627  tomatoes                                   2737 
2838   celery                                     2685 
3187   chicken broth                              2411 
15038  sour cream                                 2372 
4683   cream cheese                               2348 
...             ...                                ... 
7784   heinz sauce flavoured                      1    
7788   heirloom green beans kentucky wonder       1    
7791   heirloom tomatoes preferably green orange  1    
7753   hearty farmhousestyle bread                1    
7752   hearty country bread unsliced              1    
7749   heartshaped cinnamon candies powder        1    
7724   hazelnut flavored syrup                    1    
7707   hatch mexico green chile peppers           1    
7708   haupia layer                               1    
7711   havarti cheese folded                      1    
7712   havarti gouda cheese                       1    
7713   havartipepper cheese                       1    
7714   hawaiian barbeque sauce                    1    
7717   hawaiian buns                              1    
7719   hawaiian style marinade                    1    
7722   hawaiianstyle dinner                       1    
7723   hawaij                                     1    
7730   hazelnuts almonds                          1    
7748   heartshaped baking molds                   1    
7733   hazelnuts pistachios                       1    
7735   hazelnuts skins                            1    
7736   headless shrimp                            1    
7737   headon shrimp                              1    
7738   healthy wheat english muffins              1    
7739   heaping bar spoon powdered sugar           1    
7740   heart palm                                 1    
7742   hearthealthy condensed cream chicken soup  1    
7745   hearts romaine dole salad blend            1    
7747   hearts romaine lettuce leaves              1    
18407  zwieback toast crumbs                      1    

[18408 rows x 2 columns]

In [45]:
save_sparse_csr("sparse_recipe_ingredient_matrix", recipe_ingredient_matrix2)

In [46]:
!aws s3 cp sparse_recipe_ingredient_matrix.npz s3://RecipeVectors

upload: ./sparse_recipe_ingredient_matrix.npz to s3://RecipeVectors/sparse_recipe_ingredient_matrix.npz


In [47]:
ingred_cooccurrence_matrix = (recipe_ingredient_matrix2.T * recipe_ingredient_matrix2)

print ingred_cooccurrence_matrix.nnz
print ingred_cooccurrence_matrix.size
print ingred_cooccurrence_matrix.shape

936508
936508
(18408, 18408)


In [48]:
save_sparse_csr('ingred_cooccurrence_matrix', ingred_cooccurrence_matrix) #csc matrix also apparently works
!aws s3 cp ingred_cooccurrence_matrix.npz s3://RecipeVectors

upload: ./ingred_cooccurrence_matrix.npz to s3://RecipeVectors/ingred_cooccurrence_matrix.npz


In [49]:
svd2 = TruncatedSVD(n_components=50)
reduced_cooccurrence_matrix = svd2.fit_transform(ingred_cooccurrence_matrix)

print type(reduced_cooccurrence_matrix)
print reduced_cooccurrence_matrix.size
print reduced_cooccurrence_matrix.shape

<type 'numpy.ndarray'>
920400
(18408, 50)


In [50]:
with open('reduced_cooccurrence_matrix.pkl', 'wb') as f:
    pickle.dump(reduced_cooccurrence_matrix, f)
    
!aws s3 cp reduced_cooccurrence_matrix.pkl s3://RecipeVectors

upload: ./reduced_cooccurrence_matrix.pkl to s3://RecipeVectors/reduced_cooccurrence_matrix.pkl


# Google Part of Speech Tagging

Very slow and repeatedly hit quota. Should refactor and usee nltk or other tagger.

In [31]:
from google.auth import compute_engine
def syntax_text(text):
    """Detects syntax in the text."""
    client = language.LanguageServiceClient(credentials = compute_engine.Credentials())

    if isinstance(text, six.binary_type):
        text = text.decode('utf-8')

    # Instantiates a plain text document.
    document = types.Document(
        content=text,
        type=enums.Document.Type.PLAIN_TEXT)

    # Detects syntax in the document. You can also analyze HTML with:
    #   document.type == enums.Document.Type.HTML
    tokens = client.analyze_syntax(document).tokens

    # part-of-speech tags from enums.PartOfSpeech.Tag
    pos_tag = ('UNKNOWN', 'ADJ', 'ADP', 'ADV', 'CONJ', 'DET', 'NOUN', 'NUM',
               'PRON', 'PRT', 'PUNCT', 'VERB', 'X', 'AFFIX')

    token_pos_dict = OrderedDict()
    for token in tokens:
        #print(u'{}: {}'.format(pos_tag[token.part_of_speech.tag], token.text.content))
        if token.text.content not in token_pos_dict:
            token_pos_dict[token.text.content] = pos_tag[token.part_of_speech.tag]
        else:
            #print "{} token already in dict".format(token.text.content)
            pass
    return token_pos_dict

In [32]:
d = syntax_text('three cored and peeled green tomatoes')
# print
# for k, v in d.iteritems():
#     print "word: {} -> tag: {}".format(k, v)

print

def pos_dict_to_str(d):
    # Takes an OrderedDict that maps each ingredient to a POS
    # Returns a string containing only ingredient words that are nouns or adjectives
    pos_tags_to_remove = ('UNKNOWN', 'ADP', 'ADV', 'CONJ', 'DET', 'NUM', 'PRON', 'PRT', 'PUNCT', 'VERB', 'X', 'AFFIX')
    # keep only nouns and adjectives
    #d_keep = {k:v for k, v in d.iteritems() if v not in pos_tags_to_remove}
    d_keep = OrderedDict((k, v) for k, v in d.iteritems() if v not in pos_tags_to_remove)

    #     for k, v in d_keep.iteritems():
    #         print "word: {} -> tag: {}".format(k, v)

    keep_str = ' '.join('{}'.format(key) for key, val in d_keep.iteritems())
    #print keep_str
    return keep_str

noun_adj_str = pos_dict_to_str(d)

In [43]:
ingred_list = [u'3 avocados - peeled, pitted, and mashed',
 u'1 lime, juiced',
 u'1 teaspoon salt',
 u'1/2 cup diced onion',
 u'3 tablespoons chopped fresh cilantro',
 u'2 roma (plum) tomatoes, diced',
 u'1 teaspoon minced garlic',
 u'1 pinch ground cayenne pepper (optional)',
 u'Add all ingredients to list',
 u'Add all ingredients to list']

for ingred_str in ingred_list:
    full_d = syntax_text(ingred_str)
    reduced_str = pos_dict_to_str(full_d)
    #print
    #print reduced_str
    print "-----------"

NUM: 3
NOUN: avocados
PUNCT: -
VERB: peeled
PUNCT: ,
VERB: pitted
PUNCT: ,
, token already in dict
CONJ: and
ADJ: mashed
avocados mashed
-----------
NUM: 1
NOUN: lime
PUNCT: ,
VERB: juiced
lime
-----------
NUM: 1
NOUN: teaspoon
NOUN: salt
teaspoon salt
-----------
NUM: 1
X: /
NUM: 2
NOUN: cup
NOUN: diced
NOUN: onion
cup diced onion
-----------
NUM: 3
NOUN: tablespoons
VERB: chopped
ADJ: fresh
NOUN: cilantro
tablespoons fresh cilantro
-----------
X: 2
NOUN: roma
PUNCT: (
NOUN: plum
PUNCT: )
NOUN: tomatoes
PUNCT: ,
VERB: diced
roma plum tomatoes
-----------
NUM: 1
NOUN: teaspoon
VERB: minced
NOUN: garlic
teaspoon garlic
-----------
NUM: 1
NOUN: pinch
NOUN: ground
NOUN: cayenne
NOUN: pepper
PUNCT: (
ADJ: optional
PUNCT: )
pinch ground cayenne pepper optional
-----------
VERB: Add
DET: all
NOUN: ingredients
PRT: to
VERB: list
ingredients
-----------
VERB: Add
DET: all
NOUN: ingredients
PRT: to
VERB: list
ingredients
-----------


In [36]:
def do_google_api_processing(ingredient_string):
    # takes one ingredient string
    d = syntax_text(ingredient_string)
    noun_adj_str = pos_dict_to_str(d)
    return noun_adj_str
    
    
def reduce_ingreds_list(ingreds_list):
    reduced_ingreds_list = [do_google_api_processing(unidecode.unidecode(ingred_str)) for ingred_str in ingreds_list]
    return reduced_ingreds_list

#df['POS_cleaned_ingredients'] = df['ingredients'].apply(reduce_ingreds_list)

#df[['ingredients','POS_cleaned_ingredients']].sample(40)

subset_df = df.sample(40)

from IPython.display import display
display(subset_df)

categories cookingTime  \
8964   [Relishes, Sauces and Condiments, Everyday Coo...     PT1H45M   
11818  [Grain Side Dishes, Side Dishes, Everyday Cook...       PT45M   
13976  [Vegetarian Lasagna, Spinach Lasagna, Lasagna,...     PT2H29M   
3967   [Italian Recipes, Pasta by Shape, Vegetarian L...        PT1H   
10572  [Everyday Cooking, Main Dishes, Recipes, Summe...        PT1H   
15285  [Salmon Recipes, Fish Recipes, Everyday Cookin...       PT20M   
9546   [Spicy Appetizers, Chicken Appetizers, Buffalo...       PT20M   
12409  [Dips and Spreads, Appetizers and Snacks, Mexi...       PT40M   
6985   [Snack Chips, Snack Recipes, Appetizers and Sn...       PT30M   
9808   [Chicken Breasts, Baked Chicken Breasts, Baked...       PT30M   
729    [Mexican Recipes, Everyday Cooking, Main Dishe...       PT35M   
663    [Scandinavian Recipes, Swedish Recipes, Swedis...     PT1H25M   
870    [Soup, Soups, Stews and Chili, Dumplings, Chin...     PT1H15M   
15138  [Breakfast Drinks, Breakfast and Brunch, Veggi...       PT15M   
459    [Cucumber Salad, Vegetable Salads, Vegetarian ...     PT1H20M   
9028   [Clam Recipes, Shrimp Recipes, Pasta by Shape,...       PT55M   
2542   [Lemon Desserts, Banana Desserts, Fruit Desser...        PT5M   
26999  [Pancakes, Breakfast and Brunch, Bread Recipes...       PT40M   
2689   [Noodles, Pasta Main Dishes, Everyday Cooking,...       PT40M   
7149   [Japanese Recipes, Asian Recipes, Stir-Fries, ...       PT31M   
9325   [Chicken Thighs, Everyday Cooking, Main Dishes...       PT50M   
5435   [Chicken and Rice Soup, Chicken Soup, Soup, So...         NaN   
14780  [Breakfast Drinks, Breakfast and Brunch, Banan...        PT5M   
5921   [Chocolate Desserts, Chocolate Fudge, Fudge, C...         NaN   
5591   [Swanson®, Campbell's Kitchen, Trusted Brands,...       PT35M   
8601   [Filipino Recipes, Asian Recipes, Custards and...      PT2H5M   
10545  [Everyday Cooking, Main Dishes, Recipes, Pinot...      PT1H5M   
1517   [Seafood Soup, Cream Soups, Soup, Bisque, Soup...       PT35M   
5960   [Jell-O® Salad, Dessert Salads, Specialty Dess...         NaN   
396    [Potato Side Dishes, Potato Casserole Side Dis...     PT1H15M   
2948   [Japanese Recipes, Asian Recipes, Noodles, Pas...     PT1H11M   
6437   [Pasta by Shape, Pasta Main Dishes, Main Dishe...         NaN   
12237  [Holiday Cakes, Cake Recipes, Desserts, Everyd...         NaN   
14630  [Banana Muffins, Muffins, Banana Bread, Fruit ...       PT40M   
4326   [Indian Recipes, Asian Recipes, Chicken Legs, ...     PT2H25M   
9560   [Italian Recipes, Ham Recipes, Calzones, Every...     PT1H25M   
12882  [Beef Meatloaf, Meatloaf, Main Dishes, Recipes...     PT1H30M   
17299  [Cranberry Pie, Fruit Pies, Pie Recipes, Cranb...     PT2H30M   
2142   [Challah, Egg Bread, Yeast Bread, Holiday Brea...     PT1H30M   
801    [Turkey Chili, Chili, Soups, Stews and Chili, ...       PT50M   

                                             description  \
8964   This quick and very dirty recipe for black oni...   
11818                                                NaN   
13976                                                NaN   
3967                                                 NaN   
10572                                                NaN   
15285                                                NaN   
9546                                                 NaN   
12409                                                NaN   
6985                                                 NaN   
9808                                                 NaN   
729                                                  NaN   
663    Our family's traditional Christmas recipe, fre...   
870    A simple, light 'Chinese dumpling' classic ......   
15138                                                NaN   
459                                                  NaN   
9028                                                 NaN   
2542                                                 NaN   
26999        

In [50]:
%%time

sample_lst = np.squeeze(subset_df[['ingredients']].values)[32]
print sample_lst

reduced_sample_lst = reduce_ingreds_list(sample_lst)
print reduced_sample_lst

further_cleaned_lst = extract_ingredients(reduced_sample_lst)
print further_cleaned_lst

#subset_df['POS_cleaned_ingredients'] = subset_df['ingredients'].apply(reduce_ingreds_list)
#display(subset_df)

[u'1 cup all-purpose flour', u'1 cup white sugar', u'1 egg', u'1 teaspoon baking soda', u'1 teaspoon vanilla extract', u'1 (16 ounce) can fruit cocktail', u'1/2 cup packed brown sugar', u'Add all ingredients to list', u'Add all ingredients to list']
['cup purpose flour', 'cup white sugar', 'egg', 'teaspoon baking soda', 'teaspoon vanilla extract', 'ounce fruit cocktail', 'cup brown sugar', 'ingredients', 'ingredients']
['purpose flour', 'white sugar', 'egg', 'baking soda', 'vanilla extract', 'fruit cocktail', 'brown sugar']
CPU times: user 492 ms, sys: 152 ms, total: 644 ms
Wall time: 5.07 s


In [52]:
%%time

subset_df['POS_cleaned_ingredients'] = subset_df['ingredients'].apply(reduce_ingreds_list)
display(subset_df)

categories cookingTime  \
8964   [Relishes, Sauces and Condiments, Everyday Coo...     PT1H45M   
11818  [Grain Side Dishes, Side Dishes, Everyday Cook...       PT45M   
13976  [Vegetarian Lasagna, Spinach Lasagna, Lasagna,...     PT2H29M   
3967   [Italian Recipes, Pasta by Shape, Vegetarian L...        PT1H   
10572  [Everyday Cooking, Main Dishes, Recipes, Summe...        PT1H   
15285  [Salmon Recipes, Fish Recipes, Everyday Cookin...       PT20M   
9546   [Spicy Appetizers, Chicken Appetizers, Buffalo...       PT20M   
12409  [Dips and Spreads, Appetizers and Snacks, Mexi...       PT40M   
6985   [Snack Chips, Snack Recipes, Appetizers and Sn...       PT30M   
9808   [Chicken Breasts, Baked Chicken Breasts, Baked...       PT30M   
729    [Mexican Recipes, Everyday Cooking, Main Dishe...       PT35M   
663    [Scandinavian Recipes, Swedish Recipes, Swedis...     PT1H25M   
870    [Soup, Soups, Stews and Chili, Dumplings, Chin...     PT1H15M   
15138  [Breakfast Drinks, Breakfast and Brunch, Veggi...       PT15M   
459    [Cucumber Salad, Vegetable Salads, Vegetarian ...     PT1H20M   
9028   [Clam Recipes, Shrimp Recipes, Pasta by Shape,...       PT55M   
2542   [Lemon Desserts, Banana Desserts, Fruit Desser...        PT5M   
26999  [Pancakes, Breakfast and Brunch, Bread Recipes...       PT40M   
2689   [Noodles, Pasta Main Dishes, Everyday Cooking,...       PT40M   
7149   [Japanese Recipes, Asian Recipes, Stir-Fries, ...       PT31M   
9325   [Chicken Thighs, Everyday Cooking, Main Dishes...       PT50M   
5435   [Chicken and Rice Soup, Chicken Soup, Soup, So...         NaN   
14780  [Breakfast Drinks, Breakfast and Brunch, Banan...        PT5M   
5921   [Chocolate Desserts, Chocolate Fudge, Fudge, C...         NaN   
5591   [Swanson®, Campbell's Kitchen, Trusted Brands,...       PT35M   
8601   [Filipino Recipes, Asian Recipes, Custards and...      PT2H5M   
10545  [Everyday Cooking, Main Dishes, Recipes, Pinot...      PT1H5M   
1517   [Seafood Soup, Cream Soups, Soup, Bisque, Soup...       PT35M   
5960   [Jell-O® Salad, Dessert Salads, Specialty Dess...         NaN   
396    [Potato Side Dishes, Potato Casserole Side Dis...     PT1H15M   
2948   [Japanese Recipes, Asian Recipes, Noodles, Pas...     PT1H11M   
6437   [Pasta by Shape, Pasta Main Dishes, Main Dishe...         NaN   
12237  [Holiday Cakes, Cake Recipes, Desserts, Everyd...         NaN   
14630  [Banana Muffins, Muffins, Banana Bread, Fruit ...       PT40M   
4326   [Indian Recipes, Asian Recipes, Chicken Legs, ...     PT2H25M   
9560   [Italian Recipes, Ham Recipes, Calzones, Every...     PT1H25M   
12882  [Beef Meatloaf, Meatloaf, Main Dishes, Recipes...     PT1H30M   
17299  [Cranberry Pie, Fruit Pies, Pie Recipes, Cranb...     PT2H30M   
2142   [Challah, Egg Bread, Yeast Bread, Holiday Brea...     PT1H30M   
801    [Turkey Chili, Chili, Soups, Stews and Chili, ...       PT50M   

                                             description  \
8964   This quick and very dirty recipe for black oni...   
11818                                                NaN   
13976                                                NaN   
3967                                                 NaN   
10572                                                NaN   
15285                                                NaN   
9546                                                 NaN   
12409                                                NaN   
6985                                                 NaN   
9808                                                 NaN   
729                                                  NaN   
663    Our family's traditional Christmas recipe, fre...   
870    A simple, light 'Chinese dumpling' classic ......   
15138                                                NaN   
459                                                  NaN   
9028                                                 NaN   
2542                                                 NaN   
26999        

CPU times: user 22.6 s, sys: 10 s, total: 32.6 s
Wall time: 4min 13s


In [81]:
svd200 = TruncatedSVD(n_components=200)
reduced_cooccurrence_matrix_200 = svd200.fit_transform(ingred_cooccurrence_matrix)

print type(reduced_cooccurrence_matrix_200)
print reduced_cooccurrence_matrix_200.size
print reduced_cooccurrence_matrix_200.shape

<type 'numpy.ndarray'>
3586200
(17931, 200)


In [82]:
with open('reduced_cooccurrence_matrix_200.pkl', 'wb') as f:
    pickle.dump(reduced_cooccurrence_matrix_200, f)
    
!aws s3 cp reduced_cooccurrence_matrix_200.pkl s3://RecipeVectors

upload: ./reduced_cooccurrence_matrix_200.pkl to s3://RecipeVectors/reduced_cooccurrence_matrix_200.pkl


# Recipes from Better Homes and Gardens

In [6]:
!aws s3 cp s3://RecipeVectors/bhg_recipes.json recipes


download: s3://RecipeVectors/bhg_recipes.json to recipes/bhg_recipes.json


In [41]:
fname = 'bhg_recipes.json'
df_bhg = pd.read_json('recipes/'+fname, dtype={})

In [42]:
len(df_bhg)

3293

In [43]:
df_bhg.dropna(axis=0, how='any')
len(df_bhg)

3293

In [45]:
df_bhg.sample(10)

ethnicCategory                                        ingredients  \
1554        mexican  [\n                    , \n                   ...   
3079          asian  [\n                    , 8, \n                ...   
2665          asian  [\n                    , 5, \n                ...   
1959          asian  [\n                    , 1, \n                ...   
3164        mexican  [\n                    , 10, \n               ...   
1172        italian  [\n                    , 1 1/2, \n            ...   
2280        italian  [\n                    , 1, \n                ...   
835         italian  [\n                    , 1, \n                ...   
2039        italian  [\n                    , 2, \n                ...   
1386          asian  [\n                    , 2, \n                ...   

                                       instructionSteps  \
1554  [Line a 3-1/2 or 4-quart slow cooker with a pl...   
3079  [Preheat oven to 425 degrees F. Sprinkle chick...   
2665  [In a medium bowl whisk together 3 Tbsp. of th...   
1959  [Sprinkle chicken lightly with salt and pepper...   
3164  [For stale tortillas: Cut each tortilla into e...   
1172  [For sauce: In a blender combine half-and-half...   
2280  [For Cilantro Pesto, place cilantro, orange ju...   
835   [Remove 1 tsp. zest and squeeze 2 Tbsp. juice ...   
2039  [Place each chicken breast portion between two...   
1386  [In a colander run hot water over frozen veget...   

                                                   name  \
1554                                    Breakfast Migas   
3079  Pan-Roasted Chicken Thighs with Thai Coconut S...   
2665                       Sesame Chicken with Broccoli   
1959                              Peanut Satay Stir-Fry   
3164                       Chipotle Chicken Chilaquiles   
1172                                Creamy Walnut Pasta   
2280          Pan-Seared Pork Chops with Cilantro Pesto   
835                                         Paleo Pesto   
2039                                    Chicken Picatta   
1386                             Oriental-Style Chicken   

                                      recipeCollections  \
1554  [Best-Ever Slow Cooker Ideas, Recipes With 400...   
3079  [Recipes With 400 Calories or Less, Best Chick...   
2665  [Recipes With 400 Calories or Less, Best Chick...   
1959  [Best-Ever Slow Cooker Ideas, Recipes With 400...   
3164  [Recipes With 400 Calories or Less, Best Chick...   
1172  [Best Chicken Breast Recipes, 30 Minute Dinner...   
2280  [30 Minute Dinner Ideas, Simple Garden-Fresh S...   
835   [Recipes With 400 Calories or Less, Best Chick...   
2039  [Best-Ever Slow Cooker Ideas, Recipes With 400...   
1386  [Best-Ever Slow Cooker Ideas, Recipes With 400...   

                                      relatedCategories  \
1554  [Breakfast and Brunch Recipes, Casseroles, Din...   
3079  [Asian Recipes, Chicken Recipes, Chicken Thigh...   
2665  [Asian Recipes, Boneless Chicken, Boneless Chi...   
1959  [Asian Recipes, Boneless Chicken Recipes, Chic...   
3164  [Casseroles, Chicken Recipes, Dinner Recipes, ...   
1172   [Dinner Recipes, Italian Recipes, Pasta Recipes]   
2280             [Pork Recipes, Salad Dressing Recipes]   
835   [Dinner Recipes, Italian Recipes, Pasta Recipe...   
2039  [Boneless Chicken, Boneless Chicken Recipes, C...   
1386  [Asian Recipes, Chicken Recipes, Dinner Recipe...   

                                                    url  
1554    http://www.bhg.com/recipe/pork/breakfast-migas/  
3079  http://www.bhg.com/recipe/pan-roasted-chicken-...  
2665  http://www.bhg.com/recipe/sesame-chicken-with-...  
1959   http://www.bhg.com/recipe/peanut-satay-stir-fry/  
3164  http://www.bhg.com/recipe/chipotle-chicken-chi...  
1172     http://www.bhg.com/recipe/creamy-walnut-pasta/  
2280  http://www.bhg.com/recipe/pan-seared-pork-chop...  
835              http://www.bhg.com/recipe/paleo-pesto/  
2039         http://www.bhg.com/recipe/chicken-picatta/  
1386  http

In [46]:
def clean_bhg_ingredients(orig_ingred_list):
    ingred_str = ' '.join(orig_ingred_list)
    stripped = [s.strip() for s in ingred_str.splitlines()]
    stripped_empty_removed = filter(None, stripped)
    rem_numbers = [x for x in stripped_empty_removed if not any(c.isdigit() for c in x)]
    return rem_numbers



In [47]:
from tqdm import tqdm
tqdm.pandas()

In [48]:
df_bhg['cleanedIngredients'] = df_bhg['ingredients'].progress_apply(clean_bhg_ingredients)

100%|██████████| 3293/3293 [00:00<00:00, 13983.36it/s]


In [49]:
df_bhg = df_bhg[df_bhg.cleanedIngredients.astype(str) != '[]']
len(df_bhg)

3291

In [50]:
df_bhg.sample(10)

ethnicCategory                                        ingredients  \
2067          asian  [\n                    , 2, \n                ...   
1049        italian  [\n                    , 1, \n                ...   
2576          asian  [\n                    , 12, \n               ...   
1161        italian  [\n                    , 1/3, \n              ...   
2606        italian  [\n                    , 1/3, \n              ...   
2119          asian  [\n                    , 2, \n                ...   
3269          asian  [\n                    , 8, \n                ...   
617         mexican  [\n                    , 3 - 4, \n            ...   
1683        mexican  [\n                    , 1, \n                ...   
657         mexican  [\n                    , 6, \n                ...   

                                       instructionSteps  \
2067  [In a large bowl, combine eggs, soy sauce, ric...   
1049  [Chop enough of the eggplant to make 1 cup. Ha...   
2576  [Drain tofu; press out excess liquid with pape...   
1161  [In a food processor combine the 1/3 cup olive...   
2606  [For sauce, in a medium saucepan cook onion an...   
2119  [In a 1-gallon freezer bag combine beef tips w...   
3269  [Trim fat from lamb. Partially freeze lamb. Th...   
617   [Trim fat from meat; cut ribs into serving-siz...   
1683  [In a large bowl, stir together ground pasilla...   
657   [Place turkey in a resealable plastic bag set ...   

                                      name  \
2067      Sesame Crab and Brown Rice Cakes   
1049                     Ratatouille Pizza   
2576              Spicy Tofu Lettuce Wraps   
1161                 Spinach-Oregano Pesto   
2606                    Chicken Parmigiana   
2119  Make-Ahead Beef and Udon Noodle Bowl   
3269                   Greek Lamb Stir-Fry   
617            Tex-Mex Barbecued Beef Ribs   
1683                Mexican Tacos Carnitas   
657     Spicy Chipotle-Bourbon Turkey Legs   

                                      recipeCollections  \
2067  [Recipes With 400 Calories or Less, Best Chick...   
1049  [Best-Ever Slow Cooker Ideas, Recipes With 400...   
2576  [Best-Ever Slow Cooker Ideas, Recipes With 400...   
1161                       [Simple Garden-Fresh Salads]   
2606  [Best-Ever Slow Cooker Ideas, Recipes With 400...   
2119  [Best-Ever Slow Cooker Ideas, Our Favorite Cas...   
3269  [Best-Ever Slow Cooker Ideas, Recipes With 400...   
617   [Best Chicken Breast Recipes, Our Favorite Cas...   
1683  [Best-Ever Slow Cooker Ideas, Recipes With 400...   
657   [Recipes With 400 Calories or Less, Best Chick...   

                                      relatedCategories  \
2067  [Appetizers, Asian Recipes, Breakfast and Brun...   
1049  [Appetizers, Dinner Recipes, Easy Appetizers, ...   
2576  [Appetizers, Asian Recipes, Easy Appetizers, E...   
1161                           [Salad Dressing Recipes]   
2606  [Chicken Recipes, Dinner Recipes, Ethnic Recip...   
2119  [Asian Recipes, Beef Recipes, Dinner Recipes, ...   
3269  [Asian Recipes, Dinner Recipes, Ethnic Recipes...   
617   [Beef Recipes, Dinner Recipes, Ethnic Recipes,...   
1683  [Christmas Recipes, Dinner Recipes, Ethnic Rec...   
657   [Dinner Recipes, Ethnic Recipes, Grilling Reci...   

                                                    url  \
2067  http://www.bhg.com/recipe/appetizers-snacks/se...   
1049  http://www.bhg.com/recipe/sandwiches/ratatouil...   
2576  http://www.bhg.com/recipe/chicken/spicy-tofu-l...   
1161   http://www.bhg.com/recipe/spinach-oregano-pesto/   
2606  http://www.bhg.com/recipe/chicken/chicken-parm...   
2119  http://www.bhg.com/recipe/make-ahead-beef-and-...   
3269  http://www.bhg.com/recipe/meat/greek-lamb-stir...   
617   http://www.bhg.com/recipe/meat/tex-mex-barbecu...   
1683  http://www.bhg.com/recipe/pork/mexican-tacos-c...   
657   http://www.bhg.com/recipe/spicy-chipotle-bourb...   

                                     cleanedIngredients  
2067  [eggs, lightly beat

In [51]:
from cleaning_util import extract_ingredients, translate_non_alphanumerics

In [52]:
df_bhg['cleanedIngredients'] = df_bhg['cleanedIngredients'].progress_apply(extract_ingredients)

100%|██████████| 3291/3291 [00:04<00:00, 810.07it/s]


In [53]:
df_bhg.sample(10)

ethnicCategory                                        ingredients  \
2057        mexican  [\n                    , \n                   ...   
2577          asian  [\n                    , 12, \n               ...   
2697        italian  [\n                    , 1, \n                ...   
1151          asian  [\n                    , 2, \n                ...   
2988          asian  [\n                    , 1/2, \n              ...   
3035         french  [\n                    , 1, \n                ...   
1621        mexican  [\n                    , 2, \n                ...   
432         mexican  [\n                    , 1, \n                ...   
1294        italian  [\n                    , 8, \n                ...   
386         mexican  [\n                    , 2, \n                ...   

                                       instructionSteps  \
2057  [Lightly coat an unheated medium skillet with ...   
2577  [For easier slicing, partially freeze meat. Tr...   
2697  [On a lightly floured surface, roll bread doug...   
1151  [For sauce, in a small bowl stir together wate...   
2988  [For dressing, in small bowl, stir together li...   
3035  [Preheat oven to 325 degrees F. Line two large...   
1621  [In a 4-qt. Dutch oven combine first six ingre...   
432   [In a 2-quart microwave-safe casserole micro-c...   
1294  [Cook pasta according to package directions in...   
386   [In a large dry skillet, toast ancho peppers o...   

                                     name  \
2057                        Chicken Chili   
2577               Szechwan Beef Stir-Fry   
2697  Canadian Bacon and Sauerkraut Pizza   
1151                 Peppers and Zucchini   
2988       Asian Chicken and Cabbage Slaw   
3035              French Filled Macaroons   
1621          Chicken Taco Tortilla Soup    
432              Hot Mexican Potato Salad   
1294                    Fusilli Primavera   
386         Pork Tenderloin with Red Mole   

                                      recipeCollections  \
2057  [Best-Ever Slow Cooker Ideas, Recipes With 400...   
2577  [Recipes With 400 Calories or Less, Best Chick...   
2697  [Best-Ever Slow Cooker Ideas, Recipes With 400...   
1151  [Best-Ever Slow Cooker Ideas, Recipes With 400...   
2988  [Best-Ever Slow Cooker Ideas, Recipes With 400...   
3035  [Best-Ever Slow Cooker Ideas, 30 Minute Dinner...   
1621  [Best-Ever Slow Cooker Ideas, Our Favorite Cas...   
432   [Best-Ever Slow Cooker Ideas, Recipes With 400...   
1294  [Best-Ever Slow Cooker Ideas, Recipes With 400...   
386   [Best-Ever Slow Cooker Ideas, Recipes With 400...   

                                      relatedCategories  \
2057  [Boneless Chicken Recipes, Chicken Breast Reci...   
2577  [Asian Recipes, Beef Recipes, Dinner Recipes, ...   
2697  [Dinner Recipes, Ethnic Recipes, Healthy Dinne...   
1151  [Asian Recipes, Ethnic Recipes, Healthy Recipe...   
2988  [Asian Recipes, Chicken Recipes, Dinner Recipe...   
3035  [Chocolate Desserts, Christmas Cookies, Christ...   
1621                    [Mexican Recipes, Soup Recipes]   
432   [Ethnic Recipes, Healthy Recipes, Heart-Health...   
1294  [Dinner Recipes, Ethnic Recipes, Healthy Recip...   
386   [Dinner Recipes, Ethnic Recipes, Grilling Reci...   

                                                    url  \
2057     http://www.bhg.com/recipe/soups/chicken-chili/   
2577  http://www.bhg.com/recipe/beef/szechwan-beef-s...   
2697  http://www.bhg.com/recipe/meat/canadian-bacon-...   
1151  http://www.bhg.com/recipe/vegetables/peppers-a...   
2988  http://www.bhg.com/recipe/poultry/asian-chicke...   
3035  http://www.bhg.com/recipe/cookies/french-fille...   
1621  http://www.bhg.com/recipe/chicken-taco-tortill...   
432   http://www.bhg.com/recipe/salads/hot-mexican-p...   
1294  http://www.bhg.com/recipe/pasta/fusilli-primav...   
386   http://www.bhg.com/recipe/pork/pork-tenderloin...   

                                     cleanedIngredients  
2057  [nonstick cooking spray, reduc

In [54]:
df_bhg.to_pickle('bhg_recipes_cleaned_ingred.pkl')

In [55]:
!aws s3 cp bhg_recipes_cleaned_ingred.pkl s3://RecipeVectors

upload: ./bhg_recipes_cleaned_ingred.pkl to s3://RecipeVectors/bhg_recipes_cleaned_ingred.pkl
